# Elektron WebSocket API MRN Example with Python

## Machine Readable News Overview

Refinitiv Machine Readable News (MRN) is an advanced service for automating the consumption and systematic analysis of news. It delivers deep historical news archives, ultra-low latency structured news and news analytics directly to your applications. This enables algorithms to exploit the power of news to seize opportunities, capitalize on market inefficiencies and manage event risk.

MRN aims for replacing the legacy News 2K (N2_UBMS and N2_STORY).

### MRN Data behavior
MRN is published over Elektron using an Open Message Model (OMM) envelope in News Text Analytics domain messages. The Real-time News content set is made available over MRN_STORY RIC. The content data is contained in a FRAGMENT field that has been compressed, and potentially fragmented across multiple messages, in order to reduce bandwidth and message size.

A FRAGMENT field has a different data type based on a connection type:
* RSSL connection (ESDK [C++](https://developers.refinitiv.com/elektron/elektron-sdk-cc)/[Java](https://developers.refinitiv.com/elektron/elektron-sdk-java)): BUFFER type
* WebSocket connection: Base64 ascii string

The data goes through the following series of transformations:

1. The core content data is a UTF-8 JSON string
2. This JSON string is compressed using gzip
3. The compressed JSON is split into a number of fragments (BUFFER or Base64 ascii string) which each fit into a single update message
4. The data fragments are added to an update message as the FRAGMENT field value in a FieldList envelope


<img src="images/mrn_process.png"/>

Therefore, in order to parse the core content data, the application will need to reverse this process. The WebSocket application also need to convert a received Base64 string in a FRAGMENT field to bytes data before further process this field.

### MRN Data model

Five fields, as well as the RIC itself, are necessary to determine whether the entire item has been received in its various fragments and how to concatenate the fragments to reconstruct the item:
* MRN_SRC: identifier of the scoring/processing system that published the FRAGMENT
* GUID: a globally unique identifier for the data item. All messages for this data item will have the same GUID values.
* FRAGMENT: compressed data item fragment, itself
* TOT_SIZE: total size in bytes of the fragmented data
* FRAG_NUM: sequence number of fragments within a data item. This is set to 1 for the first fragment of each item published and is incremented for each subsequent fragment for the same item.

A single MRN data item publication is uniquely identified by the combination of RIC, MRN_SRC, and GUID.

#### Fragmentation
For a given RIC-MRN_SRC-GUID combination, when a data item requires only a single message, then TOT_SIZE will equal the number of bytes in the FRAGMENT and FRAG_NUM will be 1.

When multiple messages are required, then the data item can be deemed as fully received once the sum of the number of bytes of each FRAGMENT equals TOT_SUM. The consumer will also observe that all FRAG_NUM range from 1 to the number of the fragment, with no intermediate integers skipped. In other words, a data item transmitted over three messages will contain FRAG_NUM values of 1, 2 and 3.

#### Compression
The FRAGMENT field is compressed with gzip compression, thus requiring the consumer to decompress to reveal the JSON plain-text data in that FID.

When an MRN data item is sent in multiple messages, all the messages must be received and their FRAGMENTs concatenated before being decompressed. In other words, the FRAGMENTs should not be decompressed independently of each other.

The decompressed output is encoded in UTF-8 and formatted as JSON.

Please see a full documentation of this example application in [this article](https://developers.refinitiv.com/article/introduction-machine-readable-news-elektron-websocket-api-refinitiv).

If you are not familiar with MRN concept, please visit the following resources which will give you a full explanation of the MRN data model and implementation logic:
* [Webinar Recording: Introduction to Machine Readable News](https://developers.refinitiv.com/news#news-accordion-nid-12045)
* [Introduction to Machine Readable News (MRN) with Elektron Message API (EMA)](https://developers.refinitiv.com/article/introduction-machine-readable-news-mrn-elektron-message-api-ema).
* [MRN Data Models and Elektron Implementation Guide](https://developers.refinitiv.com/elektron/elektron-sdk-java/docs?content=8736&type=documentation_item).
* [Machine Readable News (MRN) & N2_UBMS Comparison and Migration Guide](https://developers.refinitiv.com/article/machine-readable-news-mrn-n2_ubms-comparison-and-migration-guide).

In [1]:
# #uncomment if you do not have requests and websocket-client (version 0.49 and above) installed\n
# #Install requests and websocket-client packages in a current Jupyter kernal\n

import sys

# !{sys.executable} -m pip install requests
# !{sys.executable} -m pip install websocket-client

In [2]:

import time
import getopt
import socket
import json
import websocket
import threading
from threading import Thread, Event
import base64
import zlib
import requests

### EDP Credentials

Please put in your EDP credentials and client ID here.

In [3]:
# EDP Credentials

user = ''
password = ''
client_id = ''

In [4]:
# EDP connection variables

token = ''
token_refresh = ''
token_api_endpoint = 'https://api.refinitiv.com/auth/oauth2/v1/token'
hostname = 'apac-3.pricing.streaming.edp.thomsonreuters.com'
port = '443'
app_id = '256'
position = socket.gethostbyname(socket.gethostname())
login_id = 1

In [5]:
# WebSocket connections Variables

web_socket_app = None
web_socket_open = False
counter = 1
_news_envelopes = []

# keeps decompress news JSON messaage
_news_messages = []

### EDP Token retrival

In order to connect to ERT on Cloud, you need to retrieve token from the Token API first. This part of the code will take care of then token retrieval for you.

In [6]:
# EDP Token Retrieval

def get_token():
    print('Retrieve Token')
    data = {
        'client_id': client_id,
        'grant_type': 'password',
        'password': password,
        'scope': 'trapi',
        'takeExclusiveSignOnControl': True,
        'username': user,
    }
    #print(data)
    r = requests.post(token_api_endpoint,
        data=data,
        verify=True)
    auth_json = r.json()
    #print(json.dumps(auth_json, sort_keys=True, indent=2, separators=(',', ':')))
    response = {
        'token': '',
        'error': '',
        'refresh': ''
    }
    if ('access_token' in auth_json):
        response['token'] = auth_json['access_token']
        response['refresh'] = auth_json['refresh_token']
    else:
        response['error'] = auth_json['error_description']
    return response

# EDP Token Refresh

def refresh_token(refresh):
    print('Refresh Token')
    print(refresh)
    refresh = refresh.encode('ascii')
    
    data = {
        'client_id': client_id,
        'grant_type': 'refresh_token',
        'refresh_token': refresh,
        'username': user,
    }
    #print(data)
    r = requests.post(token_api_endpoint,
        data=data,
        verify=True)
    auth_json = r.json()
    print(json.dumps(auth_json, sort_keys=True, indent=2, separators=(',', ':')))
    response = {
        'token': '',
        'error': '',
        'refresh': ''
    }
    if ('access_token' in auth_json):
        response['token'] = auth_json['access_token']
        response['refresh'] = auth_json['refresh_token']
    else:
        response['error'] = auth_json['error_description']
    return response

### MRN Process Code

The MRN data can be subscribed with the *NewsTextAnalytics* domain and MRN-specific RIC name as following:
- *MRN_STORY*: Real-time News
- *MRN_TRNA*: News Analytics: Company and C&E assets
- *MRN_TRNA_DOC*: News Analytics: Macroeconomic News & events
- *MRN_TRSI*: News Sentiment Indices

 

In [7]:
# MRN variables

mrn_domain = 'NewsTextAnalytics'
mrn_item = 'MRN_STORY'

def send_mrn_request(ws):
    """ Create and send MRN request """
    mrn_req_json = {
        'ID': 2,
        "Domain": mrn_domain,
        'Key': {
            'Name': mrn_item
        }
    }

    ws.send(json.dumps(mrn_req_json))
    print("SENT:")
    print(json.dumps(mrn_req_json, sort_keys=True, indent=2, separators=(',', ':')))

### Initial Refresh Message
The Initial Refresh response does not contain any NTA data, all the fields related to news item and fragment are empty or 0. It contains only the relevant feed related or other static Fields. 

The application can just print out each incoming field data in a console for informational purpose or just ignore it.

In [8]:
# Process FieldList, Refresh and Status messages.

def decodeFieldList(fieldList_dict):
    for key, value in fieldList_dict.items():
        print("Name = %s: Value = %s" % (key, value))

def processRefresh(ws, message_json):

    print("RECEIVED: Refresh Message")
    decodeFieldList(message_json["Fields"])

def processStatus(ws, message_json):  # process incoming status message
    print("RECEIVED: Status Message")
    print(json.dumps(message_json, sort_keys=True, indent=2, separators=(',', ':')))

### MRN News Update messages Process Code

The updates contain only fields related to the item and the fragment. They do not contain any of the static or per-feed fields. The updates are not cached or conflated.

#### First Update
The first update contains all the fields related to the item and the first fragment, subsequent updates only contain the fields relating to the fragment they contain. The FRAG_NUM FID is set to 1 for the first Update of each item and is incremented in each subsequent Update for that item. This allows you to you to detect a missing fragment (and ensure correct order of the fragments for re-assembly). 


#### Subsequent Update and Multi Fragment Items
The subsequent update contains the fields necessary to identify the MRN data item, the order of this fragment among all the fragments for this item, and the fragment itself. The other point to note is that (for a Multi fragment item), Update messages with FRAG_NUM >1 will have fewer FIDs as the metadata is included in the first Update message (FRAG_NUM=1) for that item

#### News Fragments simple handle logic


<img src="images/mrn_flow_reconstruct.png"/>


In [9]:
def processMRNUpdate(ws, message_json):  # process incoming News Update messages

    fields_data = message_json["Fields"]
    # Dump the FieldList first (for informational purposes)
    # decodeFieldList(message_json["Fields"])

    # declare variables
    tot_size = 0
    guid = None

    try:
        # Get data for all requried fields
        fragment = base64.b64decode(fields_data["FRAGMENT"])
        frag_num = int(fields_data["FRAG_NUM"])
        guid = fields_data["GUID"]
        mrn_src = fields_data["MRN_SRC"]

        #print("GUID  = %s" % guid)
        #print("FRAG_NUM = %d" % frag_num)
        #print("MRN_SRC = %s" % mrn_src)

        if frag_num > 1:  # We are now processing more than one part of an envelope - retrieve the current details
            guid_index = next((index for (index, d) in enumerate(
                _news_envelopes) if d["guid"] == guid), None)
            envelop = _news_envelopes[guid_index]
            if envelop and envelop["data"]["mrn_src"] == mrn_src and frag_num == envelop["data"]["frag_num"] + 1:
                print("process multiple fragments for guid %s" %
                      envelop["guid"])

                #print("fragment before merge = %d" % len(envelop["data"]["fragment"]))

                # Merge incoming data to existing news envelop and getting FRAGMENT and TOT_SIZE data to local variables
                fragment = envelop["data"]["fragment"] = envelop["data"]["fragment"] + fragment
                envelop["data"]["frag_num"] = frag_num
                tot_size = envelop["data"]["tot_size"]
                print("TOT_SIZE = %d" % tot_size)
                print("Current FRAGMENT length = %d" % len(fragment))

                # The multiple fragments news are not completed, waiting.
                if tot_size != len(fragment):
                    return None
                # The multiple fragments news are completed, delete assoiclate GUID envelop
                elif tot_size == len(fragment):
                    del _news_envelopes[guid_index]
            else:
                print("Error: Cannot find fragment for GUID %s with matching FRAG_NUM or MRN_SRC %s" % (
                    guid, mrn_src))
                return None
        else:  # FRAG_NUM = 1 The first fragment
            tot_size = int(fields_data["TOT_SIZE"])
            print("FRAGMENT length = %d" % len(fragment))
            # The fragment news is not completed, waiting and add this news data to envelop object.
            if tot_size != len(fragment):
                print("Add new fragments to news envelop for guid %s" % guid)
                _news_envelopes.append({  # the envelop object is a Python dictionary with GUID as a key and other fields are data
                    "guid": guid,
                    "data": {
                        "fragment": fragment,
                        "mrn_src": mrn_src,
                        "frag_num": frag_num,
                        "tot_size": tot_size
                    }
                })
                return None

        # News Fragment(s) completed, decompress and print data as JSON to console
        if tot_size == len(fragment):
            print("decompress News FRAGMENT(s) for GUID  %s" % guid)
            decompressed_data = zlib.decompress(fragment, zlib.MAX_WBITS | 32)
            
            json_news = json.loads(decompressed_data)
            _news_messages.append(json_news)
            print("News = %s" % json_news)

    except KeyError as keyerror:
        print('KeyError exception: ', keyerror)
    except IndexError as indexerror:
        print('IndexError exception: ', indexerror)
    except binascii.Error as b64error:
        print('base64 decoding exception:', b64error)
    except zlib.error as error:
        print('zlib decompressing exception: ', error)
    # Some console environments like Windows may encounter this unicode display as a limitation of OS
    except UnicodeEncodeError as encodeerror:
        print("UnicodeEncodeError exception. Cannot decode unicode character for %s in this enviroment: " %
              guid, encodeerror)
    except Exception as e:
        print('exception: ', sys.exc_info()[0])

### JSON-OMM Process functions

In [10]:
def process_message(ws, message_json):
    """ Parse at high level and output JSON of message """
    message_type = message_json['Type']

    if message_type == "Refresh":
        if "Domain" in message_json:
            message_domain = message_json["Domain"]
            if message_domain == "Login":
                process_login_response(ws, message_json)
            elif message_domain:
                processRefresh(ws, message_json)
    elif message_type == "Update":
        if "Domain" in message_json and message_json["Domain"] == mrn_domain:
            processMRNUpdate(ws, message_json)
    elif message_type == "Status":
        processStatus(ws, message_json)
    elif message_type == "Ping":
        pong_json = {'Type': 'Pong'}
        ws.send(json.dumps(pong_json))
        print("SENT:")
        print(json.dumps(pong_json, sort_keys=True,
                         indent=2, separators=(',', ':')))


def process_login_response(ws, message_json):
    """ Send item request """
    send_mrn_request(ws)


def send_login_request(ws, refresh):
    """ Generate a login request from command line data (or defaults) and send """
    login_json = {
        'ID': 1,
        "Domain": 'Login',
        'Key': {
            #'Name': '',
            'Elements': {
                'ApplicationId': '',
                'Position': ''
            },
            'NameType': 'AuthnToken'
        }
    }

    login_json['Key']['Elements']['ApplicationId'] = app_id
    login_json['Key']['Elements']['Position'] = position
    login_json['Key']['Elements']['AuthenticationToken'] = token
    
    if (refresh == True):
        login_json['Refresh'] = False

    ws.send(json.dumps(login_json))
    print("SENT:")
    print(json.dumps(login_json, sort_keys=True, indent=2, separators=(',', ':')))

### WebSocket Process functions

In [ ]:
def on_message(ws, message):
    """ Called when message received, parse message into JSON for processing """
    print("RECEIVED: ")
    message_json = json.loads(message)
    print(json.dumps(message_json, sort_keys=True, indent=2, separators=(',', ':')))

    for singleMsg in message_json:
        process_message(ws, singleMsg)
        
def on_error(ws, error):
    """ Called when websocket error has occurred """
    print(error)
    
def on_close(ws):
    """ Called when websocket is closed """
    global web_socket_open
    print("WebSocket Closed")
    web_socket_open = False
    
def on_open(ws):
    """ Called when handshake is complete and websocket is open, send login """

    print("WebSocket successfully connected!")
    global web_socket_open
    web_socket_open = True
    send_login_request(ws, False)

def refresh_login(ws, refresh):
    # Get token
    token_result = refresh_token(refresh)
    if (token_result['token'] != ''):
        # Success
        global token    
        token = token_result['token']
        global token_refresh
        token_refresh = token_result['refresh']
    else:
        # Failed
        print(token_result['error'])
        sys.exit(2)
    send_login_request(ws, True)

if __name__ == "__main__":
    # Get token
    token_result = get_token()
    if (token_result['token'] != ''):
        # Success
        token = token_result['token']
        token_refresh = token_result['refresh']
    else:
        # Failed
        print(token_result['error'])
        sys.exit(2)
        
    # Start websocket handshake
    ws_address = "wss://{}:{}/WebSocket".format(hostname, port)
    print("Connecting to WebSocket " + ws_address + " ...")
    web_socket_app = websocket.WebSocketApp(ws_address, header=['User-Agent: Python'],
                                            on_message=on_message,
                                            on_error=on_error,
                                            on_close=on_close,
                                            subprotocols=['tr_json2'])
    web_socket_app.on_open = on_open

    # Event loop
    #wst = threading.Thread(target=web_socket_app.run_forever)
    wst = threading.Thread(target=web_socket_app.run_forever, kwargs={'sslopt': {'check_hostname': False}})
    wst.start()

    try:
        while True:
            time.sleep(1)
            counter = counter + 1
            if (counter % 250 == 0):
                refresh_login(web_socket_app, token_refresh)
    except KeyboardInterrupt:
        web_socket_app.close()

Retrieve Token
Connecting to WebSocket wss://apac-3.pricing.streaming.edp.thomsonreuters.com:443/WebSocket ...
WebSocket successfully connected!
SENT:
{
  "Domain":"Login",
  "ID":1,
  "Key":{
    "Elements":{
      "ApplicationId":"256",
      "AuthenticationToken":"eyJ0eXAiOiJhdCtqd3QiLCJhbGciOiJSUzI1NiIsImtpZCI6InZzUWg1LWI5NmF2aDlueE9rajRVZ2lIaUp0aE9IZ1YzSDg2X2JZUEs5NVkifQ.eyJkYXRhIjoie1wiY2lwaGVydGV4dFwiOlwielp3UUhCYlU0STBhWGczWUNocE1OZ1hTa2F5c1VRVEFmTnBqZDE0SkxPOWE4VUY2bTltdnhUR3AtS0I4cmQ2c1NxUUVtTXlmeUI3U1Q5cUczUGc5eGxCM0M2OE5YSzlUSElVTThFNE9BSFh0ZmJyRzFZQ3M1TFU1Z2VKem44a05aZGM0T1FNbUlfNUI0XzljSlkwXzc5dkpNRGU2aHhqbG1ETTZCQTRxdm1DYnYwQXRpNlhLUWUwdU5WMUwyOTFhMWUzZHhiQjRYMlFwbmRuWjlrWWdOTUtGOTBRcXkxWVIzVEM1ektSUnpXMVBQSFJiYnBoWjEySUNTb1plcUNFQ2tfcHNIQ1BUTnpDNEdobVlieDJpWnB6WWZvZVU2b2c2SzZnUldXcHlOMktKMVU4UHd1c3NxbzlHcGl5WVhXaWFtUFhtbHRIU3J5OE9Kbnc4YjZaNHZwMlJaM1lKQkxYTHF4QTRoTGZNa3VXcHlwd1Rad0oxb2ptM0RxclpNRUdYNndEalhQX0J1d3ZZdDZvdFJNUHVZVktJYWZLbjdYV0kwOEs2VE5oOG9KZk5NemtWb3VuNUZ5N

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/41UbW/bNhD+vl9B6FO7OY5ExXUqoBhsWXGC2LJi2S2SeSgoibaYyJTCl6Bu0f/eoyg7w4YOtQzew0f3xtMdvzmkUjeFEzg8nswu/NvyunR6DtEFozyn0gn+cuIkSNbj1Qj4Dl45f/ecrC4OYLfhq5IiRb8o9EKFZDVH9RapkklU1LneU64Q44jXCpEXwiqSVbSP7muNcsIRySGIBHW64bVgO8ZJ9WpXUkHRm1KpRgbn55LWnKp+9ShpX7LzP0HtMys+DN2BP3jb3/ANHylF8tKYyg3/Hb3+Fv9x/WteN3zCZF4RtqfCBJg96qx6JJygVNX5E4q+5CXhO4oa4JksaWFPntdcmShQDOyhOTkg7GIXEV4geCvrilaHDRdUNjWXDCqCtrUwVYBSAdoTZepovBDGW6dQCcb7CNJRgmVaAZkdUGLC5r0N16DFDGlCaDipAoOi9+8E3HeBPwg8D61XoTmPed6Eb1FYNwcoUams2hn62UGhB7ZMSBUKSiAcfH9jcOYOzrC3Onrvu677AJolJUUF+YPWTwt3htbcdJvJnUHRBNsjQZtaKNtGFN2KJ4J2otZNe7gTVfTN/1i3Niv0rIkAH8bU5AU5MJPjqbU/Y9cdYA/fP3l+GD4v8FWlq/sRXl43d+nHaJv5f2TJbfJ8vT18zY01l4qYOVhsYRKg6StIWpOdORLloLCH7oXt6tAAhWEPnWI3jhmJ8wZ6x+g1on5hBRUmmbSdIUPqLFVEaZgyB+KoQEszHfBG6uyR5qodv3Hg4QFw4wC/80BGgV1x0ooprNOWmg

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/41UUVOjMBB+v1+RyZM3pTWAVM1brbR2RmgPwVrPm5u0pBULASHpXefG/34b0OqNV0cedr9kN7vLl938wSyVoxhTLCZ937G81eAGG5ipOOFiwStMv2N/QgPXG4X4h4HnebwFZ49XFVtxFCYZp2j/Z5kd4nQsYhFEutR2UIsQSsidGLBFkiZy+9Fh/QV5rET8i5drZKI2OroT4bbgKF+ipeLpQfV1b4CJygpUybyEOu/ESFSSpSmP0YIVkFtu0YE3fX/agdp6G5akbJ7yne//k4BrJNinnHVYd8OFRFeSlfLDv7asV85OgCzgzKo5ewmQFx+zZtl7AgQ8Y+W6OuzFcSKTXLAUJWKZlxnTq9egAS/yUiZihRZ5VjCxBeZdcTbtgIVVuYClUGkKfbJMykr2S84k1z2kc7aJ07bMsL5uajodQrq34HnPWZwmgoNX3UwGct0b4939ogOHILgY45/7M9Aboilq1z7GPqaMfQxAGYkuc9fpPy1CHMt0vKG/6M6ix+Dab7nrlrp4KO377kM6iB7tliMzFbVmjj6tu0iPxXipByMIqEmIeQoWf0Qn4+nhOKqnJGVipaBuyMUFWLNmXHTrYurAGsamWWDJf8vDImWJ9ivKfJPEvIR9/4qGQQ/Cwa6aQ9dIBcOIIb+kqtI8gKVS8we+kPWU9ugR7AyornNIzUGt7Fr2GnlZqzOQHjW/nYOO6Jlfq34t3etaDWupDQHtPw0vjm1y6pzYxyem/lGL9sJG98/D2TNy3egZjb0GuFEwnryB7jO+7TfgYnY+mQYNvnT9Bv

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/41X3W4iyRW+z1McITkaK7inuzHYJjcxGFveNeAF7JU2RFHRXUCFppqtqjbDRpH2HXKV19snyXeqGtuzs6NdX9DV1afO73e+U/53QxTuPm90G/rhcpTetJJ2r9FsiCpXUmfSNrp/b4weu8nkbsr7WN7fTiZhlUwG7zcHYTkYftv4R7OxKPMDtBL+Hsajm/GoSUNxoDShDxA+pTPql0bSUn2SOSmdlVtJW2E20lkS+CAL+SIcvglLVmalzmkvXiS9KFNZWkphbHOuV0W5EAWtTLl3axIQepr6R3+ttCBnRC7JSW1VqS0VUmgqNckfK+UOR3MRPZdFtZWWsrIqYLCwJS3kXNtqkVfBA7eWNOj3qFxYaV4gKmhXLQqV0bosVI7AlqWha5sFU3QjDhFNlN3AaFluyG7kHppcuRcmx+m5XiqzlYbKndRNknYnMyWK4kBi6bDN9oaPfVoKVfhzZKpCUlk5/2lnSj7hqFySlivhFDKjNE5K68ggb3aulWZZBWXYVNtSH1gPH58ZKWxlDjRFlqGlX263yjkp6QBRaXL2PonPDsgyZcKu6aAkMmOr3a40jhS0L025fRP/5ef/caR7diiO0uTqhMRaijy8J5fJCX9FqifSKusEoAUt9BtK1mq1xqm5hprzixP2F3EYiZoKx7ovLk+iuZ7rG+EEIV5fub2XQmhP39JeFUWoDhxXgNMW5bktOAwEuiutcpIeh/fNenModLUUmauM0iv+wACa6/BxinIr9EHYhwOX3VZMd8NZ5OH8G2p9XIA28uY44QtJaTuK6cPOyB

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/5VWbVMTSRD+fr9iaz9hFci+ZJNNirIqIgIBES+50rvj6mqBRcPBgmSDWFdXteweKiiCyouonMqBcmhEDiwRs+uPGTaQT/MXrmc2gU0C6KVSMz2zPU/PdD8907+zSp/e3M1GWC0Wi3V1XbvRr7DVrJLuTqpal5piIz+zbe2RWPwi+0s12znQfRNUGfJDxvTesoMMw52eRMYDpjiJzE1kZZE1TiZhvLs94b7Yys2vwBiG7tScm53NjRsHa+gqd8rcG3u9N/M5v7jk+9Kh5RYdd+MuMpco6BsqbBJ06zYy/waVupDIh04nzngLArVMkCIaucUNnM0wJb+6eEuQP+Of6dBw9iXOLiNrnRgw15H5CZnviSVib54sEsKy4DfAU4HiP6jE58rx7R3sTGDnObZXiGy/x859MnSeENnOYvsddhZ9IKGgHD60JkC3u53JZZaQ+XBvYWf/5WqVwNVyYq0QOAUGD3SLBi8oXZ2qyrT3KZqq+2G5sHRwDLFW5E/0kxyq8NM7bI9h+zHObmF7Ctv3YViCHvCjcyejS2XoHkuw/S+4AjsWdv7C9jq2t7FtY+cetl/T+T9hfm9j031q516sudmpKuwYVHXT/bTpLt4+xeyZO7mnX7AzSZdn4SMaNZE5wXz116Ed86FOkIKC72i8XIx/Q+L8V0GRNY2sNWTC/zMyM8haAQofYgcC4UCp046ONS/TWIsV5PpMfTZBvQBscrD9EdsZ7DwmXrRXiQudeXCQ5zyfWdF3JOHknJGFMrPIfIXMZZKIkCpeaprrkA3YfoTtGc+AKJ

...

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/3VTXU/bMBR936+48gN7KW2SLjAsTRO0aICgMJp105YJuclNY3DtzB8p3bT/vmuK2Mv2Etsn1/Y55x7/YkL585pxpm+LRWqz9uSKDZgItURdoWP8G5vd8NvJ7GTCvg/Y0tRbKi71RMnqAXyL0BilzEbqFSipCTKwEb5qoZc1Gg6t953jo5FrhcWh1I5gO/StWTujLQaP1g0rsx7F3e9Re7s9r98ld9t7FZp0/HPPYoM2kiH4MEmSdHw4zt/cHR0le51YRfR2d8oMN67UcxNshRwi41KXeoqusrLz0mgOBfHdtEbR11hVg3RgNAgomUJhdRRRBdtjyagMNUgPRA0dqSr1WmixiiVRdWWs0aKXNjjohK5xLasBOLF1cKw3wsJcKCXWYBo4XgaYtmIp4QzJ7ZY4ou0luTukaWush0vS/tcqUiy1HPp+lH0Jk3U2jToW0U4orNA7PfwJRCsbiTX4Fxy08SB6IZVYKiw1dbOR1vmJReExdjpLsmQ/yfeztEgOeJ7y/GB4kB9+pcoWRU19QKp6NhXOdx2D/WiexdeOLgBHNpCJouusEdRrqaElE9S/3CFWTjoOn45PoTaVN5YukpHIS+LusiTJszR/W9x8PiuadNuIrdZXZxd1URzli4vT64fLD/345PF+ftHH3dp5EeN53VBAKZZK6FWgMNChGBVTyxwti21HUE5ruX5eMI+PftQpIWMd0Y8xtYTP5vwp5ASG5dwLHyj8jO7xPLhoJf1xYXmPlX96FVc8/ZgSFscpjbOMX57OdpPF+TQ+Fi8ecI4/Qgwv49

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/8WTTXPaMBCG7/0VGk0P7cQusoP50M3YkEkGjAvOpLTpZIS9gIKQqCyTMJ3+90pxMr22p160z75eydqdVz8xE+a6whTL3HRFer46Yg+zpuIgS6gx/YaznOZJjL97eK2qs60Mgxk7h6SDSBiFKJ6hcVp0SM/y1ay4l77/xhRlo5iim0YCYlrzE5dbtAOmK2Q0q9haWN2g970B8XtD0jkYlEwWKNlxyTwUeIQQK02URgelAVVgGBe1hz6YHaD5s0JMlGqnBIKKG1tVMonWgEolDSsNVEjJf6q96EX+kJCB3+8PLj+6TnLBjKlRDkarcgcHXjKBYgHa+P69tJPacF2bRAOzR7jRkJD4JPLDoCA9GoU06H4KhtFXW2n7rgSXYKvyaVwUS4oi38/gCa2U3qPL7v+blr0dd7d/c8DDQ0hIFAZhMpx085OZmAOML/abAYi7FYyiu8lNUu4fc1hv1NMXt1vWhjm/zDfWMdYpgsltw7auWXDHH6CubVqcj1YKbc4Prwk28Gw6R8G4qztqdeIVaKtnS5pPi6UTm/XSMNNYN2L7H0Ob2g3Dfqmb9SOU5sWmMe1aZUyDl7VL2uC0GQ0+pzbe0n7/JSR2XThT25FFf9hhFtJRnBQtJWmxeqX57BXyxTxt8TpLb1uajrMWssVVC/NFumgpHxeJezuG7WEJPxr3rDANPNzorWX7ni49fAJdcyX/wke/3v0GvE2HBLIDAAA=",
      "FRAG_NUM":1,
      "GUID":"Pt4lDyGp__2005212C9F4PvtFtmeE+kf8

RECEIVED: 
[
  {
    "Type":"Ping"
  }
]
SENT:
{
  "Type":"Pong"
}
RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/31VbXPiNhD+3l+x45kbktaAbV7P3wwhwF0wHBjupXRuhC2wDiO7lhzidvrfu5IhZDqdSybSWnqk3efZ1eZvgyRyGhmuwf2Hp17/cTDZG6ZBiohRHlJhuL8b/sJdrAeBh+sX89H4wzR2aVTiuS2fc5iREhzbBMdyLDV2TKvbBhGTnApI92D3Yc/yk4BzmssYZn6AS2ar1TM7jgVnmlOQOYlo1NjyDoTpKSOcUVG7XsF4mFMiaIQWZDkLKRAege38DzaiYcI4QjViyytEWRMVAAoexoQf0FdtnO5YDT6shnA3nm/gt3aja7+71wdrs5Qf0gQGRKBCF9Bs8HnLEWVZiKqijvEvzSCj+T7NTzRHijFVsUJtnYiSAzvGGFJyKIr8cst6+gB12270eu/ut1w7WyeE8B0hkuRwjNmzuEIHE6h3Gv3+W3+ooZBvPKJmWx7gxmw1ggCDQUmnPKIvSoqLbLsSrEa7p06FlEtNEbfCGPfsrtXvNtpdyFLGpbruetmJ5EcqISQZkyRhfxHJUg5C4mkBROo8OmYbM9/vtM2+jXa31bAtHdEiUa4BkxEeQWkCd7GUmdtsngRtnHiT8qZO+veYCZnmZVNVT93q1B37HkUFQTXfLVKRhCU6+YqyjkK7mM398fxp6vmwCubDjzD6Mpx4/nik9jwpkd4JyYot/xVuP/OcHRgnCURpWKj917jO53PjFhunZ9HstTtdTNIDE2FCGKq

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/7VbaW8bRxL9vr9iwE+7QIfb9zEQFhgeIkekhsxwpLUdBwvaYhxtdDgSFUS72P++1XNT08MA7JiGTXLcfCxW1/Gqque/g+3dPr4ZhIOHZDOlGAtKBmiwfbm53T183j0Pwh8GyTrcJDFczV9sBj+iwafHm1f4THZ7vwvg8XE/frz/un14DZJtccX1SONx8eLjvn35+vHu5X4H19ZPt593wV/jJP3bxwdsQqxCxj7ur1eT6HyVTIN4Mo16oM/somGy+ccBtGIGccyba2IoRRs6TrJpOluuRtOg93EWJ7NlBzowFBmlymsEYzzEuIaGr7zKsugyuI6WV/3YZ7Do+g20QJJxJIVpruEhLaCJCDH9uJ+vrjbBZHodnMdJL/R8cj7uSA37i4TSldSSkSE/gD5V1wRhaiVXDl0DNBU+22g0R1ySNrSooQX3kZoSgojAB1LXChHaR2opNGIYuxVit/d0aMEUItgptQwx94LGBpTCe6CFj66NFogZp4XIkFAvRwe71pi4pabay66FQJwJl9QqpPJ0aApbaJAhB9uoSql1yKWvQqQ+2EYlKmhBfKXmWDsUQnFoXelUaAYWghHRLguhNBReFiKIDVHUYSGU5bper/45TYNZGk+OpIL1LJ04Ih+4TGN8ROghqaGF8FEIJgxJbhwWQnker+NkEkdJkEbx8lgCi9NuApMEskxlfIQ3CQygOWzvZTSPkmgWpcERhVzOok0HGkITUqJ2GYNlDa1DBr9mli2DODlPo2PQsCjupgKAxu3Ih4esgGYktIo6PTcSLhCpLQRyox

RECEIVED: 
[
  {
    "DoNotCache":true,
    "DoNotConflate":true,
    "DoNotRipple":true,
    "Domain":"NewsTextAnalytics",
    "Fields":{
      "ACTIV_DATE":"2020-05-21",
      "FRAGMENT":"H4sIAAAAAAAC/41Ya2/byBX93l8xEFpssms7JPWyuMGitETZcvQySTuNo6AYkSOJa2qocEjLQtH/3jMPSkqRAjUC8moe93HuuXeG+VeDZuUoabgNPm5NnUHTfggbFw1aJSnjMRMN92tjOnd9jOH1+GmkBX/yyQhjMzXTr3nY10IwnWthUAvzfr3Gnza+XTSWeXKAXfLOSxJB4ny7o/xAONsLkpZsKwjlCVlVZVUw8X7BCf4m9EAcm7wLWFWyQrwnl+SmSEua8l8EGUahT2zLIh+vpPgHSXnC3kgqiGCML3i+Yzzla9Jskl2e8lKQLN+zguScRJuqEAk9XBAax3mRyGVlTlYppzxOabbgyzx/2dIXGCX7tNzUfpEk33NiXXX+RuiG0YTkKxJTsSFbWrwwmJBGr4jyXofwKwnv/PHYJeGGZRnZUEHYK40rWrIEcQuyyguWrjkRJV2tLgivtktWwKEFp0VeAZKOdUFWRb4lo4J+R9w3VBSU3EJRP9eYZWxPyg3bkrwqpUdyIcJc8M8s4UwHWu7zs53sjcVVmb4iojLPEmIAviJf+Y0zdW66ltP9Vgfge+GXez9yFfYpggWOl3EuSkLTIks5I4yKwz0ryUf/+f5q/AcRNJXBLfg+r6AdwJW0wHIithQg6Bilp6ssXW8kbJzcV1Bkty/IkoEbKiMbtuAZgDqzhCztMsolanIeqpEXLlX5VQHwMVUW9JVlZHlYcGRQKlrRmCFD4kXgyRNa5sUBJpc5LRIZ8vhaVoL1/PkYsvc0evJOAadcIPsF8V7TV0o+ek8yyB0QQA4R1I

### Real-time News Data Model
The news data appears as JSON in UTF-8 after decompression and assembly of the individual messages.
The Real-time News feed contains the headline, story body text, and associated metadata about the story as a simple group of named values.

Example JSON fields are following:
- ```firstCreated```: UTC timestamp for the first version of the story. Millisecond precision.
- ```headline```: The headline text of the news item.
- ```id```: Uniquely identifies the news item. This is the same value as the GUID in the OMM envelope.
- ```body```: The full body text of the news item (Story Body).

For more detail regarding MRN data model please visit [MRN Data Models and Elektron Implementation Guide](https://developers.refinitiv.com/elektron/elektron-sdk-java/docs?content=8736&type=documentation_item) page. If you want to compare MRN and the legacy N2_UBMS news data model, please visit [Machine Readable News (MRN) & N2_UBMS Comparison and Migration Guide](https://developers.refinitiv.com/article/machine-readable-news-mrn-n2_ubms-comparison-and-migration-guide).



In [11]:
print("first 10 headlines\n")
for news in _news_messages[:10]:
    if news["headline"]:
        print(news["headline"])

first 10 headlines

Shenwan Hongyuan Group Co Ltd - 2019 INTERIM REPORT
PDF 1: PALADIN ENERGY LTD (Share Purchase Plan Offer Document)
PDF 1: PALADIN ENERGY LTD (Share Purchase Plan Offer Document)
BREXIT-ZEW SAYS THERE IS STILL HOPE THAT A NO DEAL BREXIT CAN BE AVOIDED
HNX - CKV_20190917155723_Result of transactions of Directors PDMR Ly Chi Duc
HNX - GKM_20190917155723_Board Resolution
Announcement
إعلان
為替相場（対ドル）
삼성 QLED vs LG OLED…불붙는 `8K TV 기술전쟁`


In [12]:
print("first 10 stories\n")
for news in _news_messages[:10]:
    if news["body"]:
        print(news["body"])

first 10 stories

2019 INTERIM REPORT
For best results when printing this announcement, please click on link below:
http://pdf.reuters.com/pdfnews/pdfnews.asp?i=43059c3bf0e37541&u=urn:newsml:reuters.com:20190917:nSN6tXcL2


Please click the above URL to view the article.
Latest version of Adobe Acrobat reader is recommended to view PDF files.  The latest version of the reader can be obtained from http://www.adobe.com/products/acrobat/readstep2.html.

                             PALADIN ENERGY LTD
                                        ACN 061 681 098

17 September 2019


ASX Market Announcements                                              By Electronic Lodgement
Australian Securities Exchange
20 Bridge Street
SYDNEY NSW 2000



NOT FOR RELEASE TO U.S. WIRE SERVICES OR DISTRIBUTION IN THE UNITED STATES.

                         SHARE PURCHASE PLAN OFFER DOCUMENT
Paladin Energy Limited’s (ASX:PDN) (“Paladin” or the “Company”) provides the attached offer
documentation in respect of it

In [13]:
# #uncomment if you do not have requests and websocket-client (version 0.49 and above) installed\n
# #Install pandas and numpy packages in a current Jupyter kernal\n

# !{sys.executable} -m pip install pandas
# !{sys.executable} -m pip install numpy

In [14]:
import pandas as pd

In [15]:
df_headlines = pd.DataFrame(_news_messages, columns = ["firstCreated","messageType","provider","language","headline"])

In [16]:
messageType = {
    0: "Unknow",
    1: "Alert",
    2: "First take",
    3: "Subsequent take",
    4: "Correction",
    5: "Corrected",
    6: "Update",
    7: "Deletion",
    8: "Drop due to expiry"
}

In [17]:
df_headlines["messageType"] = [messageType[value] for value in df_headlines["messageType"] if value in messageType ]

In [18]:
df_headlines

firstCreated messageType  provider language  \
0   2019-09-17T09:01:42.835Z  First take   NS:HIIS       en   
1   2019-09-17T09:01:42.841Z  First take    NS:SGX       en   
2   2019-09-17T09:01:42.833Z  First take    NS:SGX       en   
3   2019-09-17T09:00:08.808Z       Alert   NS:RTRS       en   
4   2019-09-17T09:00:41.514Z  First take    NS:HNX       en   
5   2019-09-17T09:00:45.253Z  First take    NS:HNX       en   
6   2019-09-17T09:01:37.161Z  First take    NS:BHB       en   
7   2019-09-17T09:01:38.520Z  First take    NS:BHB       ar   
8   2019-09-16T15:01:25.665Z   Corrected   NS:KYDO       ja   
9   2019-09-17T09:01:52.643Z  First take    NS:MKN       ko   
10  2019-09-17T09:01:52.000Z  First take    NS:IFR       en   
11  2019-09-17T09:00:01.048Z  First take    NS:DJN       en   
12  2019-09-17T09:01:53.152Z  First take    NS:EGX       en   
13  2019-09-17T09:01:54.633Z  First take   NS:JIJI       en   
14  2019-09-17T09:01:27.744Z       Alert   NS:RTRS       de   
15  2019-09-17T09:01:55.204Z  First take   NS:JIJI       en   
16  2019-09-17T08:59:16.830Z       Alert   NS:RTRS       en   
17  2019-09-17T09:01:59.075Z  First take    NS:EGX       en   
18  2019-09-17T09:02:00.339Z  First take    NS:MTD       ko   
19  2019-09-17T09:02:00.468Z  First take    NS:BSE       en   
20  2019-09-17T09:01:54.967Z  First take  NS:TRLPC       en   
21  2019-09-17T08:37:54.000Z  First take   NS:RTRS       tr   
22  2019-09-17T09:02:01.503Z  First take    NS:AWP       fr   
23  2019-09-17T09:02:01.708Z  First take   NS:HNXB       en   
24  2019-09-17T09:02:02.000Z       Alert   NS:RTRS       zh   
25  2019-09-17T09:02:02.000Z       Alert   NS:RTRS       zh   
26  2019-09-17T09:02:03.030Z  First take    NS:BER       ms   
27  2019-09-17T09:02:03.268Z  First take    NS:BER       en   
28  2019-09-17T09:02:03.263Z  First take   NS:PLTS       en   
29  2019-09-17T09:02:03.396Z  First take   NS:PLTS       en   
30  2019-09-17T09:02:03.497Z  First take   NS:PLTS       en   
31  2019-09-17T09:02:03.594Z  First take   NS:PLTS       en   
32  2019-09-17T09:02:03.824Z  First take    NS:EGX       en   
33  2019-09-17T09:02:04.038Z  First take    NS:MTD       ko   
34  2019-09-17T09:02:04.000Z  First take   NS:RTRS       en   
35  2019-09-17T09:02:05.453Z  First take    NS:DJN       en   
36  2019-09-17T09:02:05.903Z  First take   NS:HNXB       en   
37  2019-09-17T09:00:48.400Z      Update   NS:HIIS       zh   
38  2019-09-17T09:00:48.409Z      Update   NS:HIIS       zh   
39  2019-09-17T09:02:04.555Z  First take    NS:MKN       ko   
40  2019-09-17T09:02:07.268Z  First take   NS:GURU       en   
41  2019-09-17T09:02:07.281Z  First take   NS:GURU       fr   
42  2019-09-17T09:02:03.287Z  First take   NS:HIIS       zh   
43  2019-09-17T09:01:15.366Z      Update   NS:HIIS       zh   
44  2019-09-17T09:01:15.375Z      Update   NS:HIIS       zh   
45  2019-09-17T09:02:07.520Z  First take   NS:HIIS       zh   
46  2019-09-17T09:01:15.558Z      Update   NS:HIIS       en   
47  2019-09-17T09:02:07.930Z  First take   NS:HIIS       en   
48  2019-09-17T09:01:16.628Z      Update   NS:HIIS       zh   
49  2019-09-17T09:01:16.636Z      Update   NS:HIIS       zh   
50  2019-09-17T09:02:08.286Z  First take   NS:HIIS       zh   
51  2019-09-17T08:55:52.000Z  First take   NS:RTRS       zh   
52  2019-09-17T09:01:16.770Z      Update   NS:HIIS       en   
53  2019-09-17T08:55:52.000Z  First take   NS:RTRS       zh   
54  2019-09-17T09:02:08.703Z  First take   NS:HIIS       en   
55  2017-10-29T21:50:24.000Z      Update   NS:RTRS       en   

                                             headline  
0   Shenwan Hongyuan Group Co Ltd - 2019 INTERIM R...  
1   PDF 1: PALADIN ENERGY LTD (Share Purchase Plan...  
2   PDF 1: PALADIN ENERGY LTD (Share Purchase Plan...  
3   BREXIT-ZEW SAYS THERE IS STILL HOPE THAT A NO ...  
4   HNX - CKV_20190917155723_Result of transaction...  
5           HNX - GKM_20190917155723_Board Resolution  
6                               

In [19]:
df_story = pd.DataFrame(_news_messages, columns = ["headline","body"])

In [20]:
df_story

headline  \
0   Shenwan Hongyuan Group Co Ltd - 2019 INTERIM R...   
1   PDF 1: PALADIN ENERGY LTD (Share Purchase Plan...   
2   PDF 1: PALADIN ENERGY LTD (Share Purchase Plan...   
3   BREXIT-ZEW SAYS THERE IS STILL HOPE THAT A NO ...   
4   HNX - CKV_20190917155723_Result of transaction...   
5           HNX - GKM_20190917155723_Board Resolution   
6                                        Announcement   
7                                               إعلان   
8                                           為替相場（対ドル）   
9                 삼성 QLED vs LG OLED…불붙는 `8K TV 기술전쟁`   
10  ALERT: China Orient Asset Management US$ 5yr/1...   
11  Press Release: WESTPAY: Hans Edin new Chief Ma...   
12  Resume of Trading on Egyptian Chemical Industr...   
13  Work to Remove Fuel from Monju Reactor Starts ...   
14   ZEW -  DIE AUSSICHTEN FÜR DIE DEUTSCHE WIRTSC...   
15  Damage from Typhoon Faxai in Japan Reaches 21....   
16  CHINA AUG ALUMINA OUTPUT IN VOLUME TERMS LOWES...   
17  Egyptian Chemical Industries (Kima) (EGCH.CA) ...   
18                  [MT리포트]17일 06시30분 '판도라 상자' 결국 열렸다   
19  GUJARAT ALKALIES & CHEMICALS LTD. - Compliance...   
20  (HK) China/Hong Kong: SCE Group signs US$246m ...   
21  Almanlar Mozaik projesini bitirmek üzereler; d...   
22  Romande Energie a acquis 10% de la jeune pouss...   
23  HNXB - 20190917_Bond_BTS_EOD09_Foreigners_Outr...   
24                                          ZEW稱前景仍負面   
25                                          ZEW称前景仍负面   
26                      BERITA RINGKAS: 17 SEPT, 2019   
27             MPOB PALM OIL PRICES (RM/MT) : SEPT 17   
28  PLATTS: 8--Bunkers MOC 37: Platts Bunker: Deli...   
29  PLATTS: 997--Spot bunkers 37: Platts Bunker: D...   
30  PLATTS: 190--Asia 2082: Platts Bunker: Deliver...   
31  PLATTS: 2--Bunkers MOC 37: Platts Bunker: Deli...   
32  Release from Atlas for Investment & Food Indus...   
33                                  아이코스처럼 쥴도 세금 오를까?   
34  NY coffee C delivery notices - SEPTEMBER 17, 2019   
35  DJ HK Bourse: Announcement From Zhaojin Mining...   
36  HNXB - 20190917_Bond_BTS_EOD01_Total_market_tr...   
37  Zhaojin Mining Industry Co Ltd - 海外監管公告(with URL)   
38  Zhaojin Mining Industry Co Ltd - 海外监管公告(with URL)   
39          왈라뷰, 22일까지 `릴레이 특가 이벤트` 진행…뷰티 제품 88%까지 할인   
40        EUR/USD Intraday: key resistance at 1.1030.   
41        EUR/USD intraday : résistance clé à 1,1030.   
42            Zhaojin Mining Industry Co Ltd - 海外監管公告   
43  Credit Suisse AG - 發行的可贖回牛熊證代號55683, 55685的剩餘價...   
44  Credit Suisse AG - 发行的可赎回牛熊证代号55683, 55685的剩余价...   
45  Credit Suisse AG - 發行的可贖回牛熊證代號55683, 55685的剩餘價...   
46  Credit Suisse AG - Notice of Valuation of Mand...   
47  Credit Suisse AG - Notice of Valuation of Mand...   
48  Credit Suisse AG - 發行的可贖回牛熊證代號53766, 55548的剩餘價...   
49  Credit Suisse AG - 发行的可赎回牛熊证代号53766, 55548的剩余价...   
50  Credit Suisse AG - 發行的可贖回牛熊證代號53766, 55548的剩餘價...   
51                中國財政：1-8月全國財政收入增長3.2%，支出增長8.8%--財政部   
52  Credit Suisse AG - Notice of Valuation of Mand...   
53                中国财政：1-8月全国财政收入增长3.2%，支出增长8.8%--财政部   
54  Credit Suisse AG - Notice of Valuation of Mand...   
55                              *TOP NEWS*-World News   

                                                 body  
0                                 2019 INTERIM REPORT  
1   For best results when printing this announceme...  
2                                PALADIN ENERGY LT...  
3                                                      
4   \r\n\r\n Double click on the URL below to view...  
5   \r\n\r\n Double click on the URL below to view...  
6      ([1]Arabic) ([2]English)\n\nReferences\n\n ...  
7      ([1]عربي) ( [2]إنجليزي)\n\nReferences\n\n  ...  
8   \n１７日\n\n（日本時間）\n\n　０時　１０８円０１－０２銭\n\n　１時　１０７円９...  
9   \n   삼성전자와 LG전자가 8K(4K·UHD의 4배 화질) TV의 화질 등 핵심...  
10      HONG KONG, Sept 17 (IFR) - \n\n\n (Reporti...  
11  \n\n   Westpay AB, leading fintech provider of...  
12  \n Section : Trading Notices                  ...  
13  Fukui, 

## References
* [Refinitiv Elektron SDK Family page](https://developers.refinitiv.com/elektron) on the [Refinitiv Developer Community](https://developers.thomsonreuters.com/) web site.
* [Refinitiv Elektron WebSocket API page](https://developers.refinitiv.com/websocket-api).
* [Developer Webinar Recording: Introduction to Electron WebSocket API](https://www.youtube.com/watch?v=CDKWMsIQfaw).
* [Introduction to Machine Readable News with Elektron WebSocket API](https://developers.refinitiv.com/article/introduction-machine-readable-news-elektron-websocket-api-refinitiv).
* [Machine Readable News (MRN) & N2_UBMS Comparison and Migration Guide](https://developers.refinitiv.com/article/machine-readable-news-mrn-n2_ubms-comparison-and-migration-guide).
* [Introduction to Machine Readable News (MRN) with Elektron Message API (EMA)](https://developers.refinitiv.com/article/introduction-machine-readable-news-mrn-elektron-message-api-ema).
* [MRN Data Models and Elektron Implementation Guide](https://developers.refinitiv.com/elektron/elektron-sdk-java/docs?content=8736&type=documentation_item).
* [Refinitiv-API-Samples/Example.WebSocketAPI.Javascript.NewsMonitor](https://github.com/Refinitiv-API-Samples/Example.WebSocketAPI.Javascript.NewsMonitor).

For any question related to this example or Elektron WebSocket API, please use the Developer Community [Q&A Forum](https://community.developers.refinitiv.com/spaces/152/websocket-api.html).